**ConnectToDeltaOnADLS**

Connect to the Delta Table created in ADF using Azure Databricks to connect to ADLS with a Service Principal

In [0]:
adlsAccountName = "<enterADLSaccountNameHere>"
sourceAdlsContainerName = "bronze"
sinkAdlsContainerName = "silver"
sourceAdlsFolderName = "diabetes"
sinkAdlsFolderName = "diabetes"

In [0]:
spark.conf.set(
    "fs.azure.account.key." + adlsAccountName + ".dfs.core.windows.net",
    dbutils.secrets.get(scope="<enterScopeHere>",key="Adls2-KeySecret"))

In [0]:
dbutils.fs.ls("abfss://" + sourceAdlsContainerName + "@" + adlsAccountName + ".dfs.core.windows.net/")

Out[3]: [FileInfo(path='abfss://bronze@cdcacceleredfkdd3zynq6k.dfs.core.windows.net/SalesLT.Customer.txt', name='SalesLT.Customer.txt', size=217829, modificationTime=1679577529000),
 FileInfo(path='abfss://bronze@cdcacceleredfkdd3zynq6k.dfs.core.windows.net/SalesLTAddress.csv', name='SalesLTAddress.csv', size=62625, modificationTime=1679577890000),
 FileInfo(path='abfss://bronze@cdcacceleredfkdd3zynq6k.dfs.core.windows.net/SalesLTProduct.csv', name='SalesLTProduct.csv', size=1358154, modificationTime=1679577891000),
 FileInfo(path='abfss://bronze@cdcacceleredfkdd3zynq6k.dfs.core.windows.net/diabetes/', name='diabetes/', size=0, modificationTime=1679700073000)]

In [0]:
SubscriptionID = dbutils.secrets.get("<enterScopeHere>","SubscriptionID")
DirectoryID = dbutils.secrets.get("<enterScopeHere>","DirectoryID")
ServicePrincipalAppID = dbutils.secrets.get("<enterScopeHere>","ServicePrincipalAppID")
ServicePrincipalSecret = dbutils.secrets.get("<enterScopeHere>","AppSecret")
ResourceGroup = dbutils.secrets.get("<enterScopeHere>","ResourceGroup")
BlobConnectionKey = dbutils.secrets.get("<enterScopeHere>","Adls2-KeySecret")

In [0]:
configs = {"fs.azure.account.auth.type": "OAuth",
           "fs.azure.account.oauth.provider.type": "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider",
           "fs.azure.account.oauth2.client.id": ServicePrincipalAppID,
           "fs.azure.account.oauth2.client.secret": ServicePrincipalSecret,
           "fs.azure.account.oauth2.client.endpoint": "https://login.microsoftonline.com/"+DirectoryID+"/oauth2/token"}

In [0]:
dbutils.fs.unmount("/mnt/source")
dbutils.fs.unmount("/mnt/sink") 

---------------------------------------------------------------------------
ExecutionError                            Traceback (most recent call last)
<command-847672408742506> in <cell line: 1>()
----> 1 dbutils.fs.unmount("/mnt/source")
      2 dbutils.fs.unmount("/mnt/sink")

/databricks/python_shell/dbruntime/dbutils.py in f_with_exception_handling(*args, **kwargs)
    360                     exc.__context__ = None
    361                     exc.__cause__ = None
--> 362                     raise exc
    363 
    364             return f_with_exception_handling

ExecutionError: An error occurred while calling o433.unmount.
: java.rmi.RemoteException: java.lang.IllegalArgumentException: requirement failed: Directory not mounted: /mnt/source; nested exception is: 
	java.lang.IllegalArgumentException: requirement failed: Directory not mounted: /mnt/source
	at com.databricks.backend.daemon.data.client.DbfsClient.send0(DbfsClient.scala:135)
	at com.databricks.backend.daemon.data.client

In [0]:
dbutils.fs.mount(
  source = "abfss://"+sourceAdlsContainerName+"@"+adlsAccountName+".dfs.core.windows.net/",
  mount_point = "/mnt/source",
  extra_configs = configs)


dbutils.fs.mount(
  source = "abfss://"+sinkAdlsContainerName+"@"+adlsAccountName+".dfs.core.windows.net/",
  mount_point = "/mnt/sink",
  extra_configs = configs)

Out[7]: True

In [0]:
dbutils.fs.ls ("/mnt/")

Out[8]: [FileInfo(path='dbfs:/mnt/sink/', name='sink/', size=0, modificationTime=0),
 FileInfo(path='dbfs:/mnt/source/', name='source/', size=0, modificationTime=0)]

In [0]:
spark.sql("CREATE DATABASE IF NOT EXISTS diabetes")
spark.sql("CREATE TABLE IF NOT EXISTS diabetes.diabetesage USING DELTA LOCATION '/mnt/sink/"+sinkAdlsFolderName+"/adfdelta/'")


Out[10]: DataFrame[]

In [0]:

%sql

SELECT * FROM diabetes.diabetesage
     

AGE SEX BMI BP S1 S2 S3 S4 S5 S6 Y Gender ageband 59 2 32.1 101.0 157 93.2 38.0 4.0 4.8598 87 151 Female RetiredAdult 48 1 21.6 87.0 183 103.2 70.0 3.0 3.8918 69 75 Male Adult 72 2 30.5 93.0 156 93.6 41.0 4.0 4.6728 85 141 Female RetiredAdult 24 1 25.3 84.0 198 131.4 40.0 5.0 4.8903 89 206 Male Adult 50 1 23.0 101.0 192 125.4 52.0 4.0 4.2905 80 135 Male Adult 23 1 22.6 89.0 139 64.8 61.0 2.0 4.1897 68 97 Male Adult 36 2 22.0 90.0 160 99.6 50.0 3.0 3.9512 82 138 Female Adult 66 2 26.2 114.0 255 185.0 56.0 4.55 4.2485 92 63 Female RetiredAdult 60 2 32.1 83.0 179 119.4 42.0 4.0 4.4773 94 110 Female RetiredAdult 29 1 30.0 85.0 180 93.4 43.0 4.0 5.3845 88 310 Male Adult 22 1 18.6 97.0 114 57.6 46.0 2.0 3.9512 83 101 Male Adult 56 2 28.0 85.0 184 144.8 32.0 6.0 3.5835 77 69 Female RetiredAdult 53 1 23.7 92.0 186 109.2 62.0 3.0 4.3041 81 179 Male Adult 50 2 26.2 97.0 186 105.4 49.0 4.0 5.0626 88 185 Female Adult 61 1 24.0 91.0 202 115.4 72.0 3.0 4.2905 73 118 Male RetiredAdult 34 2 24.7 118.0 254 184.2 39.0 7.0 5.037 81 171 Female Adult 47 1 30.3 109.0 207 100.2 70.0 3.0 5.2149 98 166 Male Adult 68 2 27.5 111.0 214 147.0 39.0 5.0 4.9416 91 144 Female RetiredAdult 38 1 25.4 84.0 162 103.0 42.0 4.0 4.4427 87 97 Male Adult 41 1 24.7 83.0 187 108.2 60.0 3.0 4.5433 78 168 Male Adult 35 1 21.1 82.0 156 87.8 50.0 3.0 4.5109 95 68 Male Adult 25 2 24.3 95.0 162 98.6 54.0 3.0 3.8501 87 49 Female Adult 25 1 26.0 92.0 187 120.4 56.0 3.0 3.9703 88 68 Male Adult 61 2 32.0 103.67 210 85.2 35.0 6.0 6.107 124 245 Female RetiredAdult 31 1 29.7 88.0 167 103.4 48.0 4.0 4.3567 78 184 Male Adult 30 2 25.2 83.0 178 118.4 34.0 5.0 4.852 83 202 Female Adult 19 1 19.2 87.0 124 54.0 57.0 2.0 4.1744 90 137 Male YoungAdult 42 1 31.9 83.0 158 87.6 53.0 3.0 4.4659 101 85 Male Adult 63 1 24.4 73.0 160 91.4 48.0 3.0 4.6347 78 131 Male RetiredAdult 67 2 25.8 113.0 158 54.2 64.0 2.0 5.2933 104 283 Female RetiredAdult 32 1 30.5 89.0 182 110.6 56.0 3.0 4.3438 89 129 Male Adult 42 1 20.3 71.0 161 81.2 66.0 2.0 4.2341 81 59 Male Adult 58 2 38.0 103.0 150 107.2 22.0 7.0 4.6444 98 341 Female RetiredAdult 57 1 21.7 94.0 157 58.0 82.0 2.0 4.4427 92 87 Male RetiredAdult 53 1 20.5 78.0 147 84.2 52.0 3.0 3.989 75 65 Male Adult 62 2 23.5 80.33 225 112.8 86.0 2.62 4.8752 96 102 Female RetiredAdult 52 1 28.5 110.0 195 97.2 60.0 3.0 5.2417 85 265 Male Adult 46 1 27.4 78.0 171 88.0 58.0 3.0 4.8283 90 276 Male Adult 48 2 33.0 123.0 253 163.6 44.0 6.0 5.425 97 252 Female Adult 48 2 27.7 73.0 191 119.4 46.0 4.0 4.852 92 90 Female Adult 50 2 25.6 101.0 229 162.2 43.0 5.0 4.7791 114 100 Female Adult 21 1 20.1 63.0 135 69.0 54.0 3.0 4.0943 89 55 Male Adult 32 2 25.4 90.33 153 100.4 34.0 4.5 4.5326 83 61 Female Adult 54 1 24.2 74.0 204 109.0 82.0 2.0 4.1744 109 92 Male Adult 61 2 32.7 97.0 177 118.4 29.0 6.0 4.9972 87 259 Female RetiredAdult 56 2 23.1 104.0 181 116.4 47.0 4.0 4.4773 79 53 Female RetiredAdult 33 1 25.3 85.0 155 85.0 51.0 3.0 4.5539 70 190 Male Adult 27 1 19.6 78.0 128 68.0 43.0 3.0 4.4427 71 142 Male Adult 67 2 22.5 98.0 191 119.2 61.0 3.0 3.989 86 75 Female RetiredAdult 37 2 27.7 93.0 180 119.4 30.0 6.0 5.0304 88 142 Female Adult 58 1 25.7 99.0 157 91.6 49.0 3.0 4.4067 93 155 Male RetiredAdult 65 2 27.9 103.0 159 96.8 42.0 4.0 4.6151 86 225 Female RetiredAdult 34 1 25.5 93.0 218 144.0 57.0 4.0 4.4427 88 59 Male Adult 46 1 24.9 115.0 198 129.6 54.0 4.0 4.2767 103 104 Male Adult 35 1 28.7 97.0 204 126.8 64.0 3.0 4.1897 93 182 Male Adult 37 1 21.8 84.0 184 101.0 73.0 3.0 3.912 93 128 Male Adult 37 1 30.2 87.0 166 96.0 40.0 4.15 5.0106 87 52 Male Adult 41 1 20.5 80.0 124 48.8 64.0 2.0 4.0254 75 37 Male Adult 60 1 20.4 105.0 198 78.4 99.0 2.0 4.6347 79 170 Male RetiredAdult 66 2 24.0 98.0 236 146.4 58.0 4.0 5.0626 96 170 Female RetiredAdult 29 1 26.0 83.0 141 65.2 64.0 2.0 4.0775 83 61 Male Adult 37 2 26.8 79.0 157 98.0 28.0 6.0 5.0434 96 144 Female Adult 41 2 25.7 83.0 181 106.6 66.0 3.0 3.7377 85 52 Female Adult 39 1 22.9 77.0 204 143.2 46.0 4.0 4.3041 74 128 Male Adult 67 2 2